# Induction Heads in Qwen2 0.5B using HookedTransformers

## Intial Setup of Environment

### Installing Dependencies

This section is designed to install the necessary packages and libraries for the project. This is very lightweight since it only requires only _TransformerLens_, _CircuitVis_, and _Eindex_.

In [ ]:
%%capture

!pip install transformer_lens
!pip install circuitsvis
!pip install eindex
!pip install transformers

### Importing libraries and other packages


In [ ]:
!pip install --upgrade numpy


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.1/62.1 kB 4.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.6/16.6 MB 63.5 MB/s eta 0:00:00
  Attempting uninstall: numpy
    Found existing installation: numpy 1.26.4
    Uninstalling numpy-1.26.4:
      Successfully uninstalled numpy-1.26.4
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
transformer-lens 2.16.1 requires numpy<2,>=1.26; python_version == "3.12", but you have numpy 2.3.4 which is incompatible.
opencv-python 4.12.0.88 requires numpy<2.3.0,>=2; python_version >= "3.9", but you have numpy 2.3.4 which is incompatible.
opencv-contrib-python 4.12.0.88 requires numpy<2.3.0,>=2; python_version >= "3.9", but you have numpy 2.3.4 which is incompatible.
opencv-python-headless 4.12.0.88 requires numpy<2.3.0,>=2; python_version >= "3.9", but you have numpy 2.3.4 which is incompatible.
tensor

In [ ]:
import os
from transformers import AutoTokenizer
import sys
from pathlib import Path
import pkg_resources
import functools
import sys
from pathlib import Path
from typing import Callable
import circuitsvis as cv
import einops
import numpy as np
import torch as t
import torch.nn as nn
import torch.nn.functional as F
from IPython.display import display
from jaxtyping import Float, Int
from torch import Tensor
from tqdm import tqdm
from transformer_lens import (
    ActivationCache,
    FactoredMatrix,
    HookedTransformer,
    HookedTransformerConfig,
    utils,
)
from transformer_lens.hook_points import HookPoint

/tmp/ipython-input-3837895401.py:5: DeprecationWarning: pkg_resources is deprecated as an API. See https://setuptools.pypa.io/en/latest/pkg_resources.html
  import pkg_resources


## Downloading the HookedTransformer model through TransformerLens

In this section, I use the model _Qwen2_ with O.5 billion parameters. Since, LayerNorm is essentially an _almost_ linear mapping to the residual stream, I can fold it with other linear operations. Other models can be also utilized for this purpose.

Check out the available models in the TransformerLens library - https://transformerlensorg.github.io/TransformerLens/generated/model_properties_table.html

In [ ]:
model = HookedTransformer.from_pretrained(
    "Qwen2-0.5B",
    center_unembed=True,
    center_writing_weights=True,
    fold_ln=True,
)

/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/661 [00:00<?, ?B/s]

`torch_dtype` is deprecated! Use `dtype` instead!


model.safetensors:   0%|          | 0.00/988M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/138 [00:00<?, ?B/s]

tokenizer_config.json: 0.00B [00:00, ?B/s]

vocab.json: 0.00B [00:00, ?B/s]

merges.txt: 0.00B [00:00, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

Loaded pretrained model Qwen2-0.5B into HookedTransformer


## Inspecting the HookedTransfomer Config
The goal here being to identify the parameters available in Qwen2, along with possible activations and parameters, along with their hook names

### Number of heads, layers and length of context window

In [ ]:
print("No of heads - ",model.cfg.n_heads)
print("No of layers - ",model.cfg.n_layers)
print("Length of context window - ",model.cfg.n_ctx)

No of heads -  14
No of layers -  24
Length of context window -  2048


### Entire Config dump

In [ ]:
model.cfg

HookedTransformerConfig:
{'NTK_by_parts_factor': 8.0,
 'NTK_by_parts_high_freq_factor': 4.0,
 'NTK_by_parts_low_freq_factor': 1.0,
 'NTK_original_ctx_len': 8192,
 'act_fn': 'silu',
 'attention_dir': 'causal',
 'attn_only': False,
 'attn_scale': np.float64(8.0),
 'attn_scores_soft_cap': -1.0,
 'attn_types': None,
 'checkpoint_index': None,
 'checkpoint_label_type': None,
 'checkpoint_value': None,
 'd_head': 64,
 'd_mlp': 4864,
 'd_model': 896,
 'd_vocab': 151936,
 'd_vocab_out': 151936,
 'decoder_start_token_id': None,
 'default_prepend_bos': False,
 'device': device(type='cuda'),
 'dtype': torch.float32,
 'eps': 1e-06,
 'experts_per_token': None,
 'final_rms': True,
 'from_checkpoint': False,
 'gated_mlp': True,
 'init_mode': 'gpt2',
 'init_weights': False,
 'initializer_range': 0.02,
 'load_in_4bit': False,
 'model_name': 'Qwen2-0.5B',
 'n_ctx': 2048,
 'n_devices': 1,
 'n_heads': 14,
 'n_key_value_heads': 2,
 'n_layers': 24,
 'n_params': 390856704,
 'normalization_type': 'RMSPre',
 '

## Sample Text for running the model

In this section, I utilize a sample text to run the model, whilst caching the activations, to study the attention patterns. The sample text is imported from the first page of Wikipedia on 16 October 2025 (Japan), the _featured article section_.



In [ ]:
text = "Angela Lansbury (October 16, 1925 – October 11, 2022) was an Irish-British and American actress, producer, and singer whose career spanned 80 years. To escape the Blitz, she moved to the U.S. in 1940, studying acting in New York City. She received three Academy Award for Best Supporting Actress nominations for her roles in Gaslight (1944), The Picture of Dorian Gray (1945), and The Manchurian Candidate (1962). On television, she starred as the sleuth Jessica Fletcher in the CBS whodunit series Murder, She Wrote (1984–1996), for which she was nominated for 12 consecutive Primetime Emmy Awards for Outstanding Lead Actress in a Drama Series. Among Lansbury's numerous accolades were five Tony Awards, six Golden Globe Awards, and a Laurence Olivier Award, as well as nominations for three Academy Awards, 18 Primetime Emmy Awards, a BAFTA Award, and a Grammy Award. She was honored with the National Medal of Arts in 1997, the Kennedy Center Honors in 2000, and the Academy Honorary Award in 2013."

### Running the model with cache and Attention Pattern study

The model is run with cache. This is different from HookedTransfomer methods, since I dont utilize hooks as of yet, but the results since would still be the same. The _{batch_dim}_ is kept True, as suggested in ARENA, since only one batch is used, and all the activations inside the model begin with the batch model dimension

Here, one can see the first implementation of the CircuitVis library. For brevity, the first 4 layers are studied. But given more compute, activation from more layers can be studied by changing the _{n_layer_study}_ parameter.

In [ ]:

logits, cache = model.run_with_cache(text, remove_batch_dim=True)
n_layer_study = 4
for i in range(n_layer_study):
  attention_here = cache["pattern", i]
  display(cv.attention.attention_patterns(model.to_str_tokens(text), attention_here))


## Checking Inductive Capabilities and Finding Induction Heads

To find induction circuits, the following must be done -

1. Create a sequence of random tokens repeated twice, prepended with the BOS token, calling this test sequence (BOS + random token + copy of random token)
2. Create detectors for previous token attention heads and induction heads (Q-composition)

For the sake for further study, current token attention head, and first token attention head detectors are also built. Whilst the former are undertstood in the context of previous token attention heads, the later are still a topic of study.

### Building different type of attention head detectors

These detectors are built on the type of pattern they display on the attention pattern visualization (offset diagnols, straight vertical lines or just the main diagnal), when the model is run on the test sequence.

In [ ]:
def current_attn_detector(cache: ActivationCache) -> list[str]:
    """
    Returns a list e.g. ["0.2", "1.4", "1.9"] of "layer.head" which you judge to be current-token heads
    """
    attn_heads = []
    for layer in range(model.cfg.n_layers):
        for head in range(model.cfg.n_heads):
            attention_pattern = cache["pattern", layer][head]
            # take avg of diagonal elements
            score = attention_pattern.diagonal().mean()
            if score > 0.4:
                attn_heads.append(f"{layer}.{head}")
    return attn_heads


def prev_attn_detector(cache: ActivationCache) -> list[str]:
    """
    Returns a list e.g. ["0.2", "1.4", "1.9"] of "layer.head" which you judge to be prev-token heads
    """
    attn_heads = []
    for layer in range(model.cfg.n_layers):
        for head in range(model.cfg.n_heads):
            attention_pattern = cache["pattern", layer][head]
            # take avg of sub-diagonal elements
            score = attention_pattern.diagonal(-1).mean()
            if score > 0.4:
                attn_heads.append(f"{layer}.{head}")
    return attn_heads


def first_attn_detector(cache: ActivationCache) -> list[str]:
    """
    Returns a list e.g. ["0.2", "1.4", "1.9"] of "layer.head" which you judge to be first-token heads
    """
    attn_heads = []
    for layer in range(model.cfg.n_layers):
        for head in range(model.cfg.n_heads):
            attention_pattern = cache["pattern", layer][head]
            # take avg of 0th elements
            score = attention_pattern[:, 0].mean()
            if score > 0.4:
                attn_heads.append(f"{layer}.{head}")
    return attn_heads

### Creating a function to generate repeated token sequence

In [ ]:
def generate_repeated_tokens(
    model: HookedTransformer, seq_len: int, batch_size: int = 1
) -> Int[Tensor, "batch_size full_seq_len"]:
    """
    Generates a sequence of repeated random tokens

    Outputs are:
        rep_tokens: [batch_size, 1+2*seq_len]
    """
    t.manual_seed(0)  # for reproducibility
    prefix = (t.ones(batch_size, 1) * model.tokenizer.bos_token_id).long()
    rep_tokens_half = t.randint(0, model.cfg.d_vocab, (batch_size, seq_len), dtype=t.int64)
    rep_tokens = t.cat([prefix, rep_tokens_half, rep_tokens_half], dim=-1)
    return rep_tokens


def run_and_cache_model_repeated_tokens(
    model: HookedTransformer, seq_len: int, batch_size: int = 1
) -> tuple[Tensor, Tensor, ActivationCache]:
    """
    Generates a sequence of repeated random tokens, and runs the model on it, returning (tokens,
    logits, cache). This function should use the `generate_repeated_tokens` function above.

    Outputs are:
        rep_tokens: [batch_size, 1+2*seq_len]
        rep_logits: [batch_size, 1+2*seq_len, d_vocab]
        rep_cache: The cache of the model run on rep_tokens
    """
    rep_tokens = generate_repeated_tokens(model, seq_len, batch_size)
    rep_logits, rep_cache = model.run_with_cache(rep_tokens)
    return rep_tokens, rep_logits, rep_cache

### Segway to install visualization dependencies and custom visualization functions

This functions are built on top of plotly library and are used for more effective visualizations downstream. For the purpose of understanding, it can be skipped. In future, the entire file for custom functions can be imported based on the tutorial.

Find the custom functions here - https://github.com/callummcdougall/ARENA_3.0/blob/main/chapter1_transformer_interp/exercises/plotly_utils.py#L124


In [ ]:
!pip install plotly-utils
!pip install eindex-callum
from eindex import eindex
from plotly_utils import *

In [ ]:
def get_log_probs(
    logits: Float[Tensor, "batch posn d_vocab"], tokens: Int[Tensor, "batch posn"]
) -> Float[Tensor, "batch posn-1"]:
    logprobs = logits.log_softmax(dim=-1)
    # We want to get logprobs[b, s, tokens[b, s+1]], in eindex syntax this looks like:
    correct_logprobs = eindex(logprobs, tokens, "b s [b s+1]")
    return correct_logprobs
import plotly_utils
import re

import einops
import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import torch as t
from jaxtyping import Float
from plotly.subplots import make_subplots
from torch import Tensor

def to_numpy(tensor):
    """
    Helper function to convert a tensor to a numpy array. Also works on lists, tuples, and numpy arrays.
    """
    if isinstance(tensor, np.ndarray):
        return tensor
    elif isinstance(tensor, (list, tuple)):
        array = np.array(tensor)
        return array
    elif isinstance(tensor, (Tensor, t.nn.parameter.Parameter)):
        return tensor.detach().cpu().numpy()
    elif isinstance(tensor, (int, float, bool, str)):
        return np.array(tensor)
    else:
        raise ValueError(f"Input to to_numpy has invalid type: {type(tensor)}")


def plot_loss_difference(log_probs, rep_str, seq_len, filename: str | None = None):
    fig = px.line(
        to_numpy(log_probs),
        hover_name=rep_str[1:],
        title=f"Per token log prob on correct token, for sequence of length {seq_len}*2 (repeated twice)",
        labels={"index": "Sequence position", "value": "Log prob"},
    ).update_layout(showlegend=False, hovermode="x unified")
    fig.add_vrect(x0=0, x1=seq_len - 0.5, fillcolor="red", opacity=0.2, line_width=0)
    fig.add_vrect(
        x0=seq_len - 0.5, x1=2 * seq_len - 1, fillcolor="green", opacity=0.2, line_width=0
    )
    fig.show()
    if filename is not None:
        fig.write_html(filename)


## Running the Model on Test Sequence

The model is ready to be run on the repeated sequence. Here, we notice the first visual diagnosis of induction heads - **noticeable improvement in loss difference**. This will correlate to the **non-convex bumps during the training of such models**. Remember, induction heads are universal



In [ ]:
seq_len = 50
batch_size = 1
(rep_tokens, rep_logits, rep_cache) = run_and_cache_model_repeated_tokens(
    model, seq_len, batch_size
)
rep_cache.remove_batch_dim()
rep_str = model.to_str_tokens(rep_tokens)
model.reset_hooks()
log_probs = get_log_probs(rep_logits, rep_tokens).squeeze()

print(f"Performance on the first half: {log_probs[:seq_len].mean():.3f}")
print(f"Performance on the second half: {log_probs[seq_len:].mean():.3f}")



Performance on the first half: -14.248
Performance on the second half: -1.707


/usr/local/lib/python3.12/dist-packages/eindex/indexing.py:288: UserWarning:

Using a non-tuple sequence for multidimensional indexing is deprecated and will be changed in pytorch 2.9; use x[tuple(seq)] instead of x[seq]. In pytorch 2.9 this will be interpreted as tensor index, x[torch.tensor(seq)], which will result either in an error or a different result (Triggered internally at /pytorch/torch/csrc/autograd/python_variable_indexing.cpp:306.)

/usr/local/lib/python3.12/dist-packages/eindex/indexing.py:292: UserWarning:

Using a non-tuple sequence for multidimensional indexing is deprecated and will be changed in pytorch 2.9; use x[tuple(seq)] instead of x[seq]. In pytorch 2.9 this will be interpreted as tensor index, x[torch.tensor(seq)], which will result either in an error or a different result (Triggered internally at /pytorch/torch/csrc/autograd/python_variable_indexing.cpp:306.)

/usr/local/lib/python3.12/dist-packages/eindex/indexing.py:296: UserWarning:

Using a non-tuple sequ

The performance on the first half of repeated sequence is -13.548, but notice the  significant improvement in the second half - minus 0.837. This is the power of induction heads.

In [ ]:
plot_loss_difference(log_probs, rep_str, seq_len)


### Plotting the Attention Pattern to visualize Induction stripes

As said before, induction leaves impressions on the attention patterns. The same quality that was exploited to built various attention heads detectors. In the case of induction heads, it will be diagnal stripes.

### Finding the exact Induction Heads in all the layers

Here, I build the Induction Head detector. Up untill now, various attention head detectors were built. But, now the intentis to built and list all the induction head as it is in all the layers for the model test sequence.


In [ ]:
def induction_attn_detector(cache: ActivationCache) -> list[str]:
    """
    Returns a list e.g. ["0.2", "1.4", "1.9"] of "layer.head" which you judge to be induction heads

    Remember - the tokens used to generate rep_cache are (bos_token, *rand_tokens, *rand_tokens)
    """
    attn_heads = []
    for layer in range(model.cfg.n_layers):
        for head in range(model.cfg.n_heads):
            attention_pattern = cache["pattern", layer][head]
            # take avg of (-seq_len+1)-offset elements
            seq_len = (attention_pattern.shape[-1] - 1) // 2
            score = attention_pattern.diagonal(-seq_len + 1).mean()
            if score > 0.4:
                attn_heads.append(f"{layer}.{head}")
    return attn_heads

In [ ]:
induction_attn_detector(rep_cache)

['9.8',
 '9.9',
 '9.12',
 '11.9',
 '11.11',
 '11.12',
 '11.13',
 '16.1',
 '16.6',
 '20.7',
 '21.12']

Whether or not the output of this function is correct or not can be easily verified from the visualizations of attention patterns itself implemented one cell before. But let's still try to see whether the output is correct or not.

In [ ]:
induction_layers = {9,11,16,21}
for i in induction_layers:
  ind_atten_ptn = rep_cache["pattern", i]
  display(cv.attention.attention_patterns(tokens=rep_str, attention = ind_atten_ptn))

Layer 9 has very weak induction heads, but Layer 11, 16 and other higher layes have more stronger.

## **Hooking Qwen2**

Finally, we utilize Qwen2 using HookedTransformer, to not just see which induction heads are more inducting based on calculation of induction scores. Here, we wont cache the activations as before but would rather access them through hook functions

### More segways for custom visualizations

Here, lie more custom functions for visualizations

In [ ]:

update_layout_set = {
    "xaxis_range",
    "yaxis_range",
    "hovermode",
    "xaxis_title",
    "yaxis_title",
    "colorbar",
    "colorscale",
    "coloraxis",
    "title_x",
    "bargap",
    "bargroupgap",
    "xaxis_tickformat",
    "yaxis_tickformat",
    "title_y",
    "legend_title_text",
    "xaxis_showgrid",
    "xaxis_gridwidth",
    "xaxis_gridcolor",
    "yaxis_showgrid",
    "yaxis_gridwidth",
    "yaxis_gridcolor",
    "showlegend",
    "xaxis_tickmode",
    "yaxis_tickmode",
    "margin",
    "xaxis_visible",
    "yaxis_visible",
    "bargap",
    "bargroupgap",
    "coloraxis_showscale",
    "xaxis_tickangle",
    "yaxis_scaleanchor",
    "xaxis_tickfont",
    "yaxis_tickfont",
}

def reorder_list_in_plotly_way(L: list, col_wrap: int):
    """
    Helper function, because Plotly orders figures in an annoying way when there's column wrap.
    """
    L_new = []
    while len(L) > 0:
        L_new.extend(L[-col_wrap:])
        L = L[:-col_wrap]
    return L_new


def imshow(tensor: Tensor, renderer=None, **kwargs):
    kwargs_post = {k: v for k, v in kwargs.items() if k in update_layout_set}
    kwargs_pre = {k: v for k, v in kwargs.items() if k not in update_layout_set}
    if ("size" in kwargs_pre) or ("shape" in kwargs_pre):
        size = kwargs_pre.pop("size", None) or kwargs_pre.pop("shape", None)
        kwargs_pre["height"], kwargs_pre["width"] = size  # type: ignore
    facet_labels = kwargs_pre.pop("facet_labels", None)
    border = kwargs_pre.pop("border", False)
    return_fig = kwargs_pre.pop("return_fig", False)
    text = kwargs_pre.pop("text", None)
    xaxis_tickangle = kwargs_post.pop("xaxis_tickangle", None)
    # xaxis_tickfont = kwargs_post.pop("xaxis_tickangle", None)
    static = kwargs_pre.pop("static", False)
    if "color_continuous_scale" not in kwargs_pre:
        kwargs_pre["color_continuous_scale"] = "RdBu"
    if "color_continuous_midpoint" not in kwargs_pre:
        kwargs_pre["color_continuous_midpoint"] = 0.0
    if "margin" in kwargs_post and isinstance(kwargs_post["margin"], int):
        kwargs_post["margin"] = dict.fromkeys(list("tblr"), kwargs_post["margin"])
    fig = px.imshow(to_numpy(tensor), **kwargs_pre).update_layout(**kwargs_post)
    if facet_labels:
        # Weird thing where facet col wrap means labels are in wrong order
        if "facet_col_wrap" in kwargs_pre:
            facet_labels = reorder_list_in_plotly_way(facet_labels, kwargs_pre["facet_col_wrap"])
        for i, label in enumerate(facet_labels):
            fig.layout.annotations[i]["text"] = label  # type: ignore
    if border:
        fig.update_xaxes(showline=True, linewidth=1, linecolor="black", mirror=True)
        fig.update_yaxes(showline=True, linewidth=1, linecolor="black", mirror=True)
    if text:
        if tensor.ndim == 2:
            # if 2D, then we assume text is a list of lists of strings
            assert isinstance(text[0], list)
            assert isinstance(text[0][0], str)
            text = [text]
        else:
            # if 3D, then text is either repeated for each facet, or different
            assert isinstance(text[0], list)
            if isinstance(text[0][0], str):
                text = [text for _ in range(len(fig.data))]
        for i, _text in enumerate(text):
            fig.data[i].update(text=_text, texttemplate="%{text}", textfont={"size": 12})
    # Very hacky way of fixing the fact that updating layout with xaxis_* only applies to first facet by default
    if xaxis_tickangle is not None:
        n_facets = 1 if tensor.ndim == 2 else tensor.shape[0]
        for i in range(1, 1 + n_facets):
            xaxis_name = "xaxis" if i == 1 else f"xaxis{i}"
            fig.layout[xaxis_name]["tickangle"] = xaxis_tickangle  # type: ignore
    return fig if return_fig else fig.show(renderer=renderer, config={"staticPlot": static})



In [ ]:
seq_len = 50
batch_size = 10
rep_tokens_10 = generate_repeated_tokens(model, seq_len, batch_size)

# We make a tensor to store the induction score for each head.
# We put it on the model's device to avoid needing to move things between the GPU and CPU,
# which can be slow.
induction_score_store = t.zeros(
    (model.cfg.n_layers, model.cfg.n_heads), device=model.cfg.device
)


def induction_score_hook(
    pattern: Float[Tensor, "batch head_index dest_pos source_pos"], hook: HookPoint
):
    """
    Calculates the induction score, and stores it in the [layer, head] position of the
    `induction_score_store` tensor.
    """
    # Take the diagonal of attn paid from each dest posn to src posns (seq_len-1) tokens back
    # (This only has entries for tokens with index>=seq_len)
    induction_stripe = pattern.diagonal(dim1=-2, dim2=-1, offset=1 - seq_len)
    # Get an average score per head
    induction_score = einops.reduce(induction_stripe, "batch head_index position -> head_index", "mean")
    # Store the result.
    induction_score_store[hook.layer(), :] = induction_score


# We make a boolean filter on activation names, that's true only on attention pattern names
pattern_hook_names_filter = lambda name: name.endswith("pattern")

# Run with hooks (this is where we write to the `induction_score_store` tensor`)
model.run_with_hooks(
    rep_tokens_10,
    return_type=None,  # For efficiency, we don't need to calculate the logits
    fwd_hooks=[(pattern_hook_names_filter, induction_score_hook)],
)



In [ ]:
# Plot the induction scores for each head in each layer
imshow(
    induction_score_store,
    labels={"x": "Head", "y": "Layer"},
    title="Induction Score by Head",
    text_auto=".2f",
    width=400,
    height=350,
)

In [ ]:
induction_attn_detector(rep_cache)

['9.8',
 '9.9',
 '9.12',
 '11.9',
 '11.11',
 '11.12',
 '11.13',
 '16.1',
 '16.6',
 '20.7',
 '21.12']